In [75]:
%%script false --no-raise-error
import zarr
from netCDF4 import Dataset
if __name__ == '__main__':
    #Todo read up on hdf5, zarr, netcdf, xarray, mpi, lustre, ceph
    # and check back with dkrz their structure, code conventions, datasets

    # Todo setup test cases proactively to ensure proper comparability and best practice

    #Todo use netcdf dataset for testing (for now) should already bet hdf5
    dest_hdf = Dataset("data/source.nc", "w", format="NETCDF4")
    print(dest_hdf.data_model)
    dest_hdf.close()

    #Todo import netcdf data through hdf5 to zarr (for now)
    dest_zarr = zarr.open_group('data/example2.zarr', mode='w')
    zarr.copy_all(dest_hdf, dest_zarr)
    dest_zarr.tree()

    #Todo conversion to netcdf

    #for hdf5 nothing needs to be done

    #for zarr (wip). netcdf is developing its own implementation
    # but that isn't available yet so I will work on something myself in the meantime

    #Todo setup Lustre and Ceph (need info on that)

    #Todo setup benchmark (prob compression, filesize, access-time, r/w-time) for sequential access

    #Todo setup benchmark for parallel access

    #Todo setup benchmark for random access

    #Todo setup benchmark for parallel with subfileing and async / I/O


In [76]:
%%script false --no-raise-error
from mpi4py import MPI
import numpy as np
import h5py

rank = MPI.COMM_WORLD.rank

# create HDF5 file
with h5py.File('data/test_ds.hdf5', 'w', driver="mpio", comm=MPI.COMM_WORLD) as hf:
    u = hf.create_dataset("u", data=np.random.rand(1_000_000, 10, 10, 1), shape=(1_000_000, 10, 10, 1), compression="gzip", chunks=True)
    v = hf.create_dataset("v", data=np.random.rand(1_000_000, 10, 10, 1), shape=(1_000_000, 10, 10, 1), compression="gzip", chunks=True)
    w = hf.create_dataset("w", data=np.random.rand(1_000_000, 10, 10, 1), shape=(1_000_000, 10, 10, 1), compression="gzip", chunks=True)
    x = hf.create_dataset("x", data=np.random.rand(1_000_000, 10, 10, 1), shape=(1_000_000, 10, 10, 1), compression="gzip", chunks=True)
    y = hf.create_dataset("y", data=np.random.rand(1_000_000, 10, 10, 1), shape=(1_000_000, 10, 10, 1), compression="gzip", chunks=True)

hf.close()   

In [4]:
from dask.distributed import Client

client = Client()
client
client.shutdown()

In [132]:
%%time# Create Testing Dataset, Change Parameters to vary size 
import xarray as xr
import numpy as np

u = np.random.rand(1_000_000, 10, 10, 1)
v = np.random.rand(1_000_000, 10, 10, 1)
w = np.random.rand(1_000_000, 10, 10, 1)
x = np.random.rand(1_000_000, 10, 10, 1)
y = np.random.rand(1_000_000, 10, 10, 1)
z = np.random.rand(1_000_000, 10, 10, 1)

ds = xr.Dataset(data_vars=dict(
                            u=(["1","2","3","4"], u),
                            v=(["1","2","3","4"], v),
                            w=(["1","2","3","4"], w),
                            x=(["1","2","3","4"], x),
                            y=(["1","2","3","4"], y),
                            z=(["1","2","3","4"], z)
                            ))

ds.to_netcdf("data/test_dataset.nc", mode="w")

ds.to_netcdf("data/test_dataset.h5", mode="w", engine="h5netcdf")

ds.to_zarr("data/test_dataset.zarr", mode="w")



CPU times: user 6.79 s, sys: 8.58 s, total: 15.4 s
Wall time: 17 s


In [133]:
#dataset creation for plotting

zarr_op_time = []
netcdf4_op_time = []
hdf5_op_time = []

zarr_calc_time = []
netcdf4_calc_time = []
hdf5_calc_time = []

In [134]:
%%script false --no-raise-error#zarr Previously used for cross-compatibility, could compare later as well
%%time
import xarray as xr
import time

for i in range(100):
    start_time = time.time()
    ds_zarr = xr.open_zarr('data/test_dataset.zarr', consolidated=True)
    zarr_op_time.append(time.time() - start_time)

In [135]:
%%script false --no-raise-error#zarr Previously used for cross-compatibility, could compare later as well
%%time 

import xarray as xr
import time

for i in range(100):
    #print(f"in cycle: {i}")
    start_time = time.time()
    max_var = ds_zarr["x"].max().compute()
    zarr_calc_time.append(time.time() - start_time)


In [136]:
%%time
import zarr
import time

for i in range(10000):
    start_time = time.time()
    ds_zarr = zarr.open(store="data/test_dataset.zarr",mode="r+" ,zarr_version=2)
    zarr_op_time.append(time.time() - start_time)

CPU times: user 312 ms, sys: 51.9 ms, total: 364 ms
Wall time: 334 ms


In [137]:
%%script false --no-raise-error#netcdf4 Previously used for cross-compatibility, could compare later as well
%%time

import xarray as xr
import time

for i in range(100):
    start_time = time.time()
    ds_netcdf4 = xr.open_dataset(filename_or_obj="data/test_dataset.nc", engine="h5netcdf", chunks={"u": 100, "v": 100, "w": 100, "x": 100, "y": 100, "z": 100, })
    netcdf4_op_time.append(time.time() - start_time)


In [138]:
%%script false --no-raise-error#netcdf4 Previously used for cross-compatibility, could compare later as well
%%time

import xarray as xr
import time

for i in range(100):
    start_time = time.time()
    max_var = ds_netcdf4["x"].max().compute()
    netcdf4_calc_time.append(time.time() - start_time)

In [139]:
%%time

import netCDF4
import time

for i in range(10000):
    start_time = time.time()
    ds_netcdf4 = netCDF4.Dataset("data/test_dataset.nc", mode="r+", format="NETCDF4")
    netcdf4_op_time.append(time.time() - start_time)


CPU times: user 12.6 s, sys: 1.61 s, total: 14.2 s
Wall time: 13 s


In [140]:
%%script false --no-raise-error#hdf5 Previously used for cross-compatibility, could compare later as well
%%time

import xarray as xr
import time

for i in range(100):
    start_time = time.time()
    ds_hdf5 = xr.open_dataset(filename_or_obj="data/test_dataset.h5", engine="h5netcdf", chunks='auto')
    hdf5_op_time.append(time.time() - start_time)

In [141]:
%%script false --no-raise-error#hdf5 Previously used for cross-compatibility, could compare later as well
%%time

import xarray as xr
import time

for i in range(100):
    start_time = time.time()
    max_var = ds_hdf5["x"].max().compute()
    hdf5_calc_time.append(time.time() - start_time)

In [142]:
%%time

import h5py
import time

for i in range(10000):
    start_time = time.time()
    ds_hdf5 = h5py.File("data/test_dataset.h5", mode="r+")
    hdf5_op_time.append(time.time() - start_time)

CPU times: user 122 ms, sys: 19.2 ms, total: 141 ms
Wall time: 136 ms


In [143]:
import pandas as pd

df_calc = pd.DataFrame()
df_calc.insert(0,"zarr_calc_time", zarr_calc_time)
df_calc.insert(1,"netcdf4_calc_time", netcdf4_calc_time)
df_calc.insert(2,"hdf5_calc_time", hdf5_calc_time)

df_op = pd.DataFrame()
df_op.insert(0,"zarr_op_time", zarr_op_time)
df_op.insert(1,"netcdf4_op_time", netcdf4_op_time)
df_op.insert(2,"hdf5_op_time", hdf5_op_time)

df_calc.to_pickle("data/plotting_df_calc.pk1")
df_op.to_pickle("data/plotting_df_op.pk1")


In [144]:
import pandas as pd

df_calc = pd.read_pickle("data/plotting_df_calc.pk1")
df_op = pd.read_pickle("data/plotting_df_op.pk1")


In [178]:
import plotly.express as px

#fig = px.box(data_frame=df_calc)
#fig.show()

#fig = px.histogram(data_frame=df_calc)
#fig.show()

fig = px.box(data_frame=df_op, log_y=True)
fig.show()

fig = px.histogram(data_frame=df_op, log_y=True, barmode="group")
fig.show()
